# Plugins

[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/rxavier/poniard/blob/master/examples/05._plugins.ipynb)

This notebook explains how Poniard's extensible plugin system works.

If you don't have it installed, please install from PyPI.

In [1]:
# %pip install poniard

Plugins can be thought of as callbacks in other machine learning frameworks (Keras, fastai, PyTorch Lightning, etc.). Generally, they are objects that do things at given points in time, for example, after each training epoch ends. They generally do not modify the existing behavior of the framework, but instead add new functionality.

These objects in Poniard are deliberetely not called callbacks because there is a priori no restriction over what they can do. However, the main concept remains the same.

In essence, plugin hooks are executed at different points during a Poniard estimator's lifetime, for example `self._run_plugin_method("on_setup_end")`. These hooks check which plugins, if any, were set during initialization, and run the corresponding hook for each of them (in this example, `self.on_setup_end()`).

Poniard includes 2 plugins out of the box.
1. Weights and Biases (`WandBPlugin`) logs configurations, metrics, plots and saves model and dataset artifacts.
2. Pandas Profiling (`PandasProfilingPlugin`) analyzes the dataset and generates an HTML report.

Extending Poniard by creating plugins is simple, as all they have to do is subclass `BasePlugin` and implement the hooks they need, leaving the rest as is.

In this instance we'll model the Adult Census dataset, a slightly more complicated classification task than in previous examples, and include both plugins.

In [2]:
import numpy as np
import pandas as pd
from sklearn.datasets import fetch_openml
from sklearn.model_selection import train_test_split

from poniard import PoniardClassifier
from poniard.plugins import WandBPlugin, PandasProfilingPlugin

# Adult Census dataset
X, y = fetch_openml(data_id=1590, return_X_y=True, as_frame=True)
category_cols = X.select_dtypes(include="category").columns
X = X.astype({col: object for col in category_cols})
y = pd.Series(np.where(y == ">50K", 1, 0), name="target")
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, stratify=y)

pnd = PoniardClassifier(numeric_threshold=80, n_jobs=-1,
                        plugins=[WandBPlugin(project="adult-demo"),
                                 PandasProfilingPlugin()])
pnd.setup(X_train, y_train)


Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: rxavier. Use `wandb login --relogin` to force relogin


Export report to file: 100%|██████████| 1/1 [00:00<00:00, 1066.17it/s]
/Users/rafxavier/Documents/Repos/personal/poniard/poniard/plugins/pandas_profiling.py:62: UserWarning: ipywidgets is not installed. HTML report will be saved to pandas_profiling_report.html
  warnings.warn(


Target info
-----------
Type: binary
Shape: (39073,)
Unique values: 2

Main metric
-----------
roc_auc

Thresholds
----------
Minimum unique values to consider a feature numeric: 80
Minimum unique values to consider a categorical high cardinality: 20

Inferred feature types
----------------------


PoniardClassifier(estimators=None, metrics=None,
    preprocess=True, scaler=standard, numeric_imputer=simple,
    custom_preprocessor=None, numeric_threshold=80,
    cardinality_threshold=20, cv=None, verbose=0,
    random_state=0, n_jobs=-1, plugins=[<poniard.plugins.wandb.WandBPlugin object at 0x10c52af40>, <poniard.plugins.pandas_profiling.PandasProfilingPlugin object at 0x15366c4c0>],
    plot_options=PoniardPlotFactory())
            

As can be seen, Pandas Profiling already created a report and saved it to the default location. If `ipywidgets` is installed, the report will be included in the output.

Meanwhile, Weights and Biases either logged in or prompted for a login, and started logging information about the run (preprocessor HTML representation, dataset, inferred types). Also, because plugins can check whether other plugins are included in a Poniard estimator (by using `self._check_plugin_used()`), wandb also uploaded the profile report.

In [3]:
pnd.fit()
pnd.show_results()

DummyClassifier:  89%|████████▉ | 8/9 [04:15<00:36, 36.49s/it]               /Users/rafxavier/Envs/poniard/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1327: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/rafxavier/Envs/poniard/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1327: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/rafxavier/Envs/poniard/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1327: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(resul

test_roc_auc  train_roc_auc  test_accuracy  \
HistGradientBoostingClassifier      0.926556       0.943651       0.870985   
XGBClassifier                       0.926146       0.958817       0.871369   
LogisticRegression                  0.908263       0.910026       0.853710   
LinearSVC                           0.908185       0.909986       0.854042   
RandomForestClassifier              0.900024       1.000000       0.851841   
GaussianNB                          0.853231       0.854038       0.645201   
KNeighborsClassifier                0.849157       0.940991       0.829806   
DecisionTreeClassifier              0.747474       1.000000       0.812607   
DummyClassifier                     0.500000       0.500000       0.760730   

                                train_accuracy  test_precision  \
HistGradientBoostingClassifier        0.883782        0.777370   
XGBClassifier                         0.901268        0.773695   
LogisticRegression                    0.855463        0.739179   
LinearSVC                             0.855591        0.743809   
RandomForestClassifier                0.999891        0.723518   
GaussianNB                            0.645760        0.398015   
KNeighborsClassifier                  0.879725        0.663129   
DecisionTreeClassifier                0.999936        0.605817   
DummyClassifier                       0.760730        0.000000   

                                train_precision  test_recall  train_recall  \
HistGradientBoostingClassifier         0.807800     0.646273      0.674912   
XGBClassifier                          0.845251     0.653868      0.719034   
LogisticRegression                     0.743101     0.600708      0.605118   
LinearSVC                              0.747844     0.595145      0.598139   
RandomForestClassifier                 0.999813     0.616752      0.999733   
GaussianNB                             0.397870     0.923735      0.923094   
KNeighborsClassifier                   0.783561     0.587336      0.687159   
DecisionTreeClassifier                 1.000000     0.622315      0.999733   
DummyClassifier                        0.000000     0.000000      0.000000   

                                 test_f1  train_f1    fit_time  score_time  
HistGradientBoostingClassifier  0.705656  0.735377    2.819997    0.242525  
XGBClassifier                   0.708627  0.777041   10.186358    0.146297  
LogisticRegression              0.662697  0.667047    1.630428    0.135551  
LinearSVC                       0.661118  0.664664    9.858193    0.096053  
RandomForestClassifier          0.665800  0.999773  155.954117    0.316352  
GaussianNB                      0.555784  0.555688    0.421639    0.127780  
KNeighborsClassifier            0.622879  0.732194    0.340522    3.114085  
DecisionTreeClassifier          0.613783  0.999866   45.361474    0.105464  
DummyClassifier                 0.000000  0.000000    0.364412    0.098719

After training has finished, WandB logs one plot per metric. However, we'll go ahead and run some additional plots.

In [4]:
pnd.plot.metrics(kind="strip", metrics=["accuracy", "roc_auc"])

Every plot produced by the PoniardPlotFactory will be logged to the wandb project and will remain an interactive Plotly plot.

In [5]:
candidates = ["XGBClassifier", "HistGradientBoostingClassifier",
              "LogisticRegression"]
pnd.predict_proba(estimator_names=candidates)
pnd.plot.roc_curve(estimator_names=candidates)

Completed: 100%|██████████| 3/3 [00:15<00:00,  5.07s/it]                     


In [6]:
pnd.predict(estimator_names=["XGBClassifier"])
pnd.plot.confusion_matrix(estimator_name="XGBClassifier")

Completed: 100%|██████████| 1/1 [00:11<00:00, 11.08s/it]


In [7]:
pnd.plot.permutation_importance(estimator_name="XGBClassifier")

In [8]:
pnd.plot.partial_dependence(estimator_name="XGBClassifier", feature="marital-status")

In [9]:
pnd.plot.partial_dependence(estimator_name="XGBClassifier", feature="age")

In [10]:
xgb = pnd.get_estimator("XGBClassifier")
xgb.fit(X_train, y_train)
xgb.score(X_test, y_test)

0.8775719111475074